In [ ]:
import pandas as pd
import numpy as np
import pymc3 as pm
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
from collections import OrderedDict
from time import time

import numpy as np
import scipy as sp
import pandas as pd

from scipy.optimize import fmin_powell
from scipy import integrate
from scipy import linalg

from sklearn.preprocessing import normalize
from sklearn import linear_model
from sklearn.utils.testing import ignore_warnings
from sklearn.exceptions import ConvergenceWarning

np.set_printoptions(precision=4, suppress=True)

from collections import Counter
from Levenshtein import distance as levenshtein_distance

sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
figsize = (15,8)
legend_fontsize = 16

from matplotlib import rc
rc('font',**{'family':'sans-serif'})
rc('text', usetex=True)
rc('text.latex',preamble=r'\usepackage[utf8]{inputenc}')
rc('text.latex',preamble=r'\usepackage[russian]{babel}')
rc('axes', **{'titlesize': '16', 'labelsize': '16'})
rc('legend', **{'fontsize': '16'})
rc('figure', **{'dpi' : 200})

# Bias-variance-noise decomposition

In [ ]:
## Оверфиттинг
## Исходная функция
orig = lambda x : np.sin(2*x)

## X-координаты точек данных
xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
num_points = len(xd)

## Данные
data = orig(xd) + np.random.normal(0, .25, num_points)

## Для рисования
xs = np.arange(xd[0]-1.5, xd[-1]+1.5, 0.01)

## Обучаем модель с регуляризацией
@ignore_warnings(category=ConvergenceWarning)
def train_model(xs, ys, alpha=0, use_lasso=False):
    if alpha == 0:
        return linear_model.LinearRegression(fit_intercept=True).fit( xs, ys )
    else:
        if use_lasso:
            return linear_model.Lasso(alpha=alpha, fit_intercept=True).fit( xs, ys )
        else:
            return linear_model.Ridge(alpha=alpha, fit_intercept=True).fit( xs, ys )

In [ ]:
## Выделение полиномиальных признаков
xs_d = np.vstack([xs ** i for i in range(1, num_points+1)]).transpose()
xd_d = np.vstack([xd ** i for i in range(1, num_points+1)]).transpose()

## Какие степени многочлена будем обучать и рисовать
set_of_powers = [ 3, 10 ]

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-2, 2))
ax.scatter(xd, data, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

for d in set_of_powers:
    if d == 0:
        print(np.mean(data))
        ax.hlines(np.mean(data), xmin=xs[0], xmax=xs[-1], label="$d=0$", linestyle="dashed")
    else:
        cur_model = train_model( xd_d[:, :d], data )
        print(cur_model.coef_)
        ax.plot(xs, cur_model.predict( xs_d[:, :d] ), linewidth=2, label="$d=%d$" % d)

ax.legend(loc="upper center", fontsize=legend_fontsize)

plt.show()

In [ ]:
N = 500
alpha = 0.00
use_lasso = True

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-5, 5))

res = []
for _ in range(N):
    cur_data = orig(xd) + np.random.normal(0, .25, num_points)
    cur_model = train_model(xd_d, cur_data, alpha, use_lasso)
    res.append(cur_model.predict( xs_d ))
    ax.plot(xs, res[-1], linewidth=.1, color="0.5")

ax.plot(xs, orig(xs), linewidth=2, label="Исходная функция", color=palette[0])
ax.scatter(xd, orig(xd), marker='*', s=150, color=palette[0])

ax.plot(xs, np.mean( res, axis=0 ), linewidth=2, label="Усреднённые предсказания", color="red")
ax.legend(loc="upper center", fontsize=legend_fontsize)
plt.show()

cur_model = linear_model.LinearRegression(fit_intercept=True).fit( xd_d[:, :d], data )

In [ ]:
test_set_size = 30
test_set_x = np.random.rand(test_set_size) * (2 + 1.5) - 1.5
test_set_xs = np.vstack([test_set_x ** i for i in range(1, 12)]).transpose()
print(test_set_xs.shape)
test_set_y = orig(test_set_xs[:,0]) + np.random.normal(0, .25, test_set_size)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.plot(xs, orig(xs), linewidth=2, label="Исходная функция", color=palette[0])
ax.scatter(test_set_xs[:,0], test_set_y, marker='*', s=150, color=palette[0])
ax.set_xlim((-1.5, 2))

def test_set_error(model, d):
    return np.mean( (test_set_y - model.predict(test_set_xs[:, :d])) ** 2 )

In [ ]:
N = 5000
use_lasso=False
alphas = np.logspace(-4, 2, num=20)
errors, biases, variances = [], [], []
for alpha in alphas:
    res, res_preds, res_test = [], [], []
    for _ in range(N):
        cur_data = orig(xd) + np.random.normal(0, .25, num_points)
        cur_model = train_model(xd_d, cur_data, alpha, use_lasso)
        res.append(test_set_error(cur_model, xd_d.shape[1]))
        res_test.append(cur_model.predict(test_set_xs))
        res_preds.append(cur_model.predict( xs_d ))
    res_test = np.array(res_test)
    avg_preds = np.mean(res_test, axis=0)
    errors.append(np.mean(res))
    biases.append(np.mean((avg_preds-orig(test_set_x))**2))
    variances.append(np.mean((res_test-avg_preds)**2))
    print("alpha = %.6f\tmean error = %.6f\tbias = %.6f\tvariance = %.6f" % (alpha, errors[-1], biases[-1], variances[-1]))

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
# plt.yscale('log')
plt.xscale('log')
ax.plot(alphas, biases, linewidth=2, label="Bias")
ax.plot(alphas, variances, linewidth=2, label="Variance")
ax.plot(alphas, np.array(biases) + np.array(variances), linewidth=2, label="Bias + Variance")
ax.plot(alphas, errors, linewidth=2, label="Ошибка на тестовом множестве", color="black")
ax.set_ylim((0, 1))
ax.set_xlim((0.001, 100))
ax.legend(fontsize=legend_fontsize)
# fig.savefig('statdecision1.pdf', bbox_inches='tight')

## Эквивалентное ядро в линейной регрессии

In [ ]:
d = 1
x_pred = 1

new_data = np.copy(data)
new_data[7] = 0
cur_model = linear_model.LinearRegression(fit_intercept=True).fit( xd_d[:, :d], new_data )

fig = plt.figure(figsize=(10,5))
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-2, 2))
ax.scatter(xd, new_data, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")
ax.plot(xs, cur_model.predict( xs_d[:, :d] ), linewidth=2, label="$d=%d$" % d)
y_pred = cur_model.predict(np.array([x_pred]).reshape(1,-1))
ax.scatter(x_pred, y_pred, marker='*', s=200)


print(data)
print(new_data)
print(y_pred)

In [ ]:
def get_one_prediction(x_pred, cur_y, d=1, data_ind=7, data=data):
    new_data = np.copy(data)
    new_data[data_ind] = cur_y
    cur_model = linear_model.LinearRegression(fit_intercept=True).fit( xd_d[:, :d], new_data )
    return cur_model.predict(np.array([x_pred]).reshape(1,-1))[0]

x_pred = 1
ys = np.arange(-1, 1, 0.1)
one_pred = [ get_one_prediction(x_pred, y) for y in ys ]
print(one_pred)

fig = plt.figure(figsize=(10,5))
ax = fig.add_subplot(111)
ax.set_xlim((ys[0], ys[-1]))
# ax.set_ylim((-2, 2))
# ax.scatter(xd, new_data, marker='*', s=120)
ax.plot(ys, [ get_one_prediction(x_pred, y) for y in ys ], linewidth=1, label="Предсказание в точке %.2f" % x_pred)
ax.plot(ys, [ get_one_prediction(x_pred, y, data_ind=2) for y in ys ], linewidth=1, label="Предсказание в точке %.2f, index = 2" % x_pred)
ax.plot(ys, [ get_one_prediction(x_pred, y, data_ind=5) for y in ys ], linewidth=1, label="Предсказание в точке %.2f, index = 5" % x_pred)
# ax.plot(xs, cur_model.predict( xs_d[:, :d] ), linewidth=2, label="$d=%d$" % d)
# y_pred = cur_model.predict(np.array([x_pred]).reshape(1,-1))
# ax.scatter(x_pred, y_pred, marker='*', s=200)
plt.legend()
plt.show()

## Добавим ещё данных

In [ ]:
## Исходная функция
orig = lambda x : np.sin(2*x)

## X-координаты точек данных
xd_large = np.arange(-1.5, 2, 0.05)
num_points_l = len(xd_large)

## Данные
data_large = orig(xd_large) + np.random.normal(0, .25, num_points_l)

## Для 
# xs = np.arange(xd_large[0]-.5, xd_large[-1]+.5, 0.01)

## Выделение полиномиальных признаков
xs_d = np.vstack([xs ** i for i in range(1, num_points+1)]).transpose()
xd_d_large = np.vstack([xd_large ** i for i in range(1, num_points+1)]).transpose()

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-5, 5))
ax.scatter(xd_large, data_large, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=2, label="Исходная функция", color="black")

set_of_powers = [ 1, 3, 10 ]

for d in set_of_powers:
    cur_model = linear_model.LinearRegression(fit_intercept=True).fit( xd_d_large[:, :d], data_large )
    ax.plot(xs, cur_model.predict( xs_d[:, :d] ), linewidth=2, label="$d=%d$" % d)

ax.legend(loc="upper center", fontsize=legend_fontsize)

plt.show()

## Регуляризация

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-5, 5))
ax.scatter(xd, data, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=2, label="Original function", color="black")

m_ridge_0 = linear_model.LinearRegression(fit_intercept=True).fit( xd_d[:, :10], data )
# linear_model.Lasso(alpha=0, fit_intercept=True).fit( xd_d[:, :12], data )
ax.plot(xs, m_ridge_0.predict( xs_d[:, :10] ), linewidth=2, label="$\\alpha=0.0$")
print(m_ridge_0.coef_)

m_ridge_1 = linear_model.Ridge(alpha=0.001, fit_intercept=True).fit( xd_d[:, :10], data )
# ax.plot(xs, m_ridge_1.predict( xs_d[:, :10] ), linewidth=2, label="$\\alpha=0.001$")
print(m_ridge_1.coef_)

m_ridge_2 = linear_model.Ridge(alpha=0.05, fit_intercept=True).fit( xd_d[:, :10], data )
ax.plot(xs, m_ridge_2.predict( xs_d[:, :10] ), linewidth=2, label="$\\alpha=0.5$")
print(m_ridge_2.coef_)

m_ridge_3 = linear_model.Ridge(alpha=1000.0, fit_intercept=True).fit( xd_d[:, :10], data )
ax.plot(xs, m_ridge_3.predict( xs_d[:, :10] ), linewidth=2, label="$\\alpha=1000.0$")
print(m_ridge_3.coef_)

ax.legend(loc="upper center", fontsize=legend_fontsize)
plt.show()

## Усреднение

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-5, 5))

res = []
for _ in range(1000):
    cur_data = orig(xd) + np.random.normal(0, .25, num_points)
#     cur_model = linear_model.Ridge(alpha=0.00, fit_intercept=True).fit( xd_d, cur_data )
    cur_model = linear_model.LinearRegression(fit_intercept=True).fit( xd_d, cur_data )
    res.append(cur_model.predict( xs_d ))
    ax.plot(xs, res[-1], linewidth=.1, color="0.5")

ax.plot(xs, orig(xs), linewidth=2, label="Original function", color=palette[0])
ax.scatter(xd, orig(xd), marker='*', s=150, color=palette[0])

ax.plot(xs, np.mean( res, axis=0 ), linewidth=2, label="Averaged predictions", color=palette[2])
plt.show()

# Байесовский вывод в линейной регрессии

In [ ]:
## Исходная функция
orig = lambda x : .5*x - .5

## X-координаты точек данных
xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
num_points = len(xd)

## Данные
data = orig(xd) + np.random.normal(0, .25, num_points)

## Для рисования
xs = np.arange(xd[0]-1.5, xd[-1]+1.5, 0.01)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-2, 2))
ax.plot(xs, orig(xs))
ax.scatter(xd, data, marker='*', s=120)
plt.show()

In [ ]:
from scipy.stats import multivariate_normal

# create data
N = 250
xs = np.linspace(-3, 3, N)
X = np.linspace(-1, 1, N)
Y = np.linspace(-1, 1, N)
X, Y = np.meshgrid(X, Y)

pos = np.empty(X.shape + (2,))
pos[:, :, 0] = X
pos[:, :, 1] = Y

def myplot_heatmap(Z):
    # Make the plot
    plt.axis('equal')
    plt.xlim((-1, 1))
    plt.ylim((-1, 1))
    plt.pcolormesh(X, Y, Z, cmap=plt.cm.jet)
    plt.scatter([-.5], [.5], marker='*', s=120)
    plt.show()

In [ ]:
cur_mu, cur_sigma = np.array([0, 0]), 2*np.array([[1, 0], [0, 1]])

Z = multivariate_normal.pdf(pos, mean=cur_mu, cov=cur_sigma)
print(Z.shape)

myplot_heatmap(Z)

In [ ]:
def myplot_sample_lines(mu, sigma, n=20, points=None):
    # Посэмплируем и порисуем прямые
    my_w = np.random.multivariate_normal(mu, sigma, n)

    # plt.axis('equal')
    for w in my_w:
        plt.plot(xs, w[0] + w[1]*xs, 'k-', lw=.4)
    plt.ylim((-3, 3))
    plt.xlim((-3, 3))
    if not points is None:
        plt.scatter(points[0], points[1], marker='*', s=200)
    plt.show()

In [ ]:
myplot_sample_lines(cur_mu, cur_sigma, 20)

In [ ]:
def get_likelihood(px, py):
    return lambda x : np.exp(-2*(x[0] + x[1]*px - py) ** 2) / (.25 * np.sqrt(2.*np.pi))

print(xd[2], data[2])
px, py = xd[2], data[2]
cur_likelihood = get_likelihood(px, py)
Z = np.array([[ cur_likelihood(pos[i, j]) for j in range(pos.shape[1])] for i in range(pos.shape[0])])

myplot_heatmap(Z)

In [ ]:
def bayesian_update(mu, sigma, x, y):
    x_matrix = np.array([[1, x]])
    sigma_n = np.linalg.inv(np.linalg.inv(sigma)+ (1 / (.25 ** 2)) * np.matmul(np.transpose(x_matrix), x_matrix) )
    mu_n = np.matmul(sigma_n, np.matmul(np.linalg.inv(sigma), np.transpose(mu)) + (1 / (.25 ** 2)) * np.matmul(np.transpose(x_matrix), np.array([y]) ) )
    return mu_n, sigma_n

In [ ]:
cur_mu, cur_sigma = bayesian_update(cur_mu, cur_sigma, px, py)
Z = multivariate_normal.pdf(pos, mean=cur_mu, cov=cur_sigma)
myplot_heatmap(Z)

In [ ]:
# Посэмплируем и порисуем прямые
myplot_sample_lines(cur_mu, cur_sigma, 20, points=[[px], [py]])

In [ ]:
px2, py2 = xd[7], data[7]
cur_likelihood = get_likelihood(px2, py2)
Z = np.array([[ cur_likelihood(pos[i, j]) for j in range(pos.shape[1])] for i in range(pos.shape[0])])
myplot_heatmap(Z)

In [ ]:
cur_mu, cur_sigma = bayesian_update(cur_mu, cur_sigma, px2, py2)
Z = multivariate_normal.pdf(pos, mean=cur_mu, cov=cur_sigma)
myplot_heatmap(Z)

In [ ]:
myplot_sample_lines(cur_mu, cur_sigma, n=20, points=[[px, px2], [py, py2]])

In [ ]:
px3, py3 = xd[-1], data[-1]
cur_likelihood = get_likelihood(px3, py3)
Z = np.array([[ cur_likelihood(pos[i, j]) for j in range(pos.shape[1])] for i in range(pos.shape[0])])
myplot_heatmap(Z)
cur_mu, cur_sigma = bayesian_update(cur_mu, cur_sigma, px3, py3)
Z = multivariate_normal.pdf(pos, mean=cur_mu, cov=cur_sigma)
myplot_heatmap(Z)
myplot_sample_lines(cur_mu, cur_sigma, n=20, points=[[px, px2, px3], [py, py2, py3]])

## Локальные признаки в линейной регрессии

In [ ]:
from sklearn.pipeline import make_pipeline
from sklearn.base import BaseEstimator, TransformerMixin

nums_gauss = [2, 5, 10]
gauss_xd, gauss_yd = xd, data

class GaussianFeatures(BaseEstimator, TransformerMixin):
    def __init__(self, N, width_factor=.5):
        self.N = N
        self.width_factor = width_factor
    
    @staticmethod
    def _gauss_basis(x, y, width, axis=None):
        arg = (x - y) / width
        return np.exp(-0.5 * np.sum(arg ** 2, axis))
        
    def fit(self, X, y=None):
        # create N centers spread along the data range
        self.centers_ = np.linspace(X.min(), X.max(), self.N)
        self.width_ = self.width_factor * (self.centers_[1] - self.centers_[0])
        return self
        
    def transform(self, X):
        return self._gauss_basis(X[:, :, np.newaxis], self.centers_, self.width_, axis=1)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-1.5, 1.5))
ax.scatter(gauss_xd, gauss_yd, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

for num_gauss in nums_gauss:
    gauss_model = make_pipeline(GaussianFeatures(num_gauss),
                                linear_model.LinearRegression())
    gauss_model.fit(xd[:, np.newaxis], data)
    yfit = gauss_model.predict(xs[:, np.newaxis])
    print("Коэффициенты с %d признаками: %s" % (num_gauss, " ".join(["%.4f" % x for x in gauss_model.get_params()['linearregression'].coef_])))
    ax.plot(xs, yfit, linewidth=2, label="%d гауссовских признак%s" % (num_gauss, "а" if num_gauss < 5 else "ов") )

ax.legend(loc="upper left", fontsize=legend_fontsize)

# tikzplotlib.clean_figure()
# tikzplotlib.save("regr_local.tex", axis_height='\\myplotheight', axis_width='\\myplotwidth')
plt.show()

In [ ]:
num_gauss = 5
gauss_model = make_pipeline(GaussianFeatures(num_gauss), linear_model.LinearRegression())
gauss_model.fit(gauss_xd[:, np.newaxis], gauss_yd)
yfit = gauss_model.predict(xs[:, np.newaxis])
mfeat = gauss_model.get_params()['gaussianfeatures']
mregr = gauss_model.get_params()['linearregression']
print("Коэффициенты с %d признаками: %s" % (num_gauss, " ".join(["%.4f" % x for x in gauss_model.get_params()['linearregression'].coef_])))
print("Свободный член: %.4f" % mregr.intercept_)

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
# ax.set_ylim((-1.5, 1.5))
ax.scatter(gauss_xd, gauss_yd, marker='*', s=120)
# ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

for i in range(mfeat.N):
    cur_yfit = [mregr.coef_[i] * mfeat._gauss_basis(x, mfeat.centers_[i], mfeat.width_) for x in xs]
    ax.plot(xs, cur_yfit, color="0.4", linewidth=1)
    ax.plot(xs, [mregr.intercept_ for _ in range(len(xs))], color="0.6", linewidth=1)

ax.plot(xs, yfit, linewidth=2)

# tikzplotlib.save("regr_local_detail.tex", axis_height='\\myplotheight', axis_width='\\myplotwidth')

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
# ax.set_ylim((-1.5, 1.5))
# ax.scatter(gauss_xd, gauss_yd, marker='*', s=120)
# ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

for i in range(mfeat.N):
    cur_yfit = [mfeat._gauss_basis(x, mfeat.centers_[i], mfeat.width_) for x in xs]
    ax.plot(xs, cur_yfit, color="0.6", linewidth=1)
#     ax.plot(xs, [mregr.intercept_ for _ in range(len(xs))], color="0.6", linewidth=1)

# tikzplotlib.save("regr_local_features.tex", axis_height='\\myplotheight', axis_width='\\myplotwidth')

# ax.plot(xs, yfit, linewidth=2)

In [ ]:
num_gauss=10

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
# ax.set_ylim((-1.5, 1.5))
ax.scatter(xd_large, data_large, marker='*', s=120)
# ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

gauss_model = make_pipeline(GaussianFeatures(num_gauss), linear_model.LinearRegression())
gauss_model.fit(gauss_xd[:, np.newaxis], gauss_yd)
yfit = gauss_model.predict(xs[:, np.newaxis])
mfeat = gauss_model.get_params()['gaussianfeatures']
mregr = gauss_model.get_params()['linearregression']

for i in range(mfeat.N):
    cur_yfit = [mregr.coef_[i] * mfeat._gauss_basis(x, mfeat.centers_[i], mfeat.width_) for x in xs]
    ax.plot(xs, cur_yfit, color="0.4", linewidth=1)
    ax.plot(xs, [mregr.intercept_ for _ in range(len(xs))], color="0.6", linewidth=1)

ax.plot(xs, yfit, linewidth=2)

# tikzplotlib.clean_figure()
# tikzplotlib.save("regr_local_large.tex", axis_height='\\myplotheight', axis_width='\\myplotwidth')

## Коронавирус

In [ ]:
d = pd.read_csv("owid-covid-data.csv")
drus = d[d['location'] == 'Russia']
drus[drus['total_cases'] > 2].tail(15)

In [ ]:
total_x_all = drus[drus['total_cases'] > 2]['total_cases'].to_numpy()
x_all = drus[drus['total_cases'] > 2]['new_cases'].to_numpy()
x_train = x_all[:50]
x_test = x_all[50:]
x_train[np.where(x_train == 0)] = 1

In [ ]:
dummy_xs = np.arange(1, len(x_train)+1).reshape(-1, 1)
dummy_xs_all = np.arange(1, len(x_all)+1).reshape(-1, 1)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.plot( total_x_all, label = 'Total cases' )
ax.plot( x_all, label = 'New cases' )
ax.vlines(len(x_train), 0, 200000, linestyle="dotted")
plt.legend(loc="north west")
plt.show()

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.plot( np.log(total_x_all), label = 'Log total cases' )
ax.plot( np.log(x_all), label = 'Log new cases' )
ax.vlines(len(x_train), 0, 15, linestyle="dotted")
plt.legend()
plt.show()

In [ ]:
model = linear_model.LinearRegression(fit_intercept=True).fit( dummy_xs, np.log(x_train))

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.plot( np.log(x_all) )
ax.plot( model.predict(dummy_xs_all) )
ax.vlines(len(x_train), 0, 15, linestyle="dotted")
plt.show()

In [ ]:
np.std(model.predict(dummy_xs) - np.log(x_train))

In [ ]:
mu_0 = np.array([0, 0])
sigma_0 = np.array([[10, 0], [0, 10]])

In [ ]:
def bayesian_update(mu, sigma, x, y, sigma_noise=.25):
    x_matrix = x.reshape(1, -1)
    sigma_n = np.linalg.inv(np.linalg.inv(sigma)+ (1 / (sigma_noise ** 2)) * np.matmul(np.transpose(x_matrix), x_matrix) )
    mu_n = np.matmul(sigma_n, np.matmul(np.linalg.inv(sigma), np.transpose(mu)) + (1 / (sigma_noise ** 2)) * np.matmul(np.transpose(x_matrix), np.array([y]) ) )
    return mu_n, sigma_n

def get_poly_features(d, x):
    return np.array([ x ** i for i in range(d+1) ])

def myplot_sample_lines(ax, d, mu, sigma, xs, n=20, points=None):
    # Посэмплируем и порисуем прямые
    my_w = np.random.multivariate_normal(mu, sigma, n)

    # plt.axis('equal')
    for w in my_w:
        ax.plot(xs, np.dot(w, get_poly_features(d, xs)), 'k-', lw=.2, alpha=.5)
    if not points is None:
        ax.scatter(points[0], points[1], marker='*', s=200)

def train_poly_model(d, xs, ys, sigma_noise=.5):
    mu_0 = np.zeros(d+1)
    sigma_0 = 10 * np.identity(d+1)
    mu, sigma = mu_0, sigma_0
    for x,y in zip(xs, ys):
        mu, sigma = bayesian_update( mu, sigma, get_poly_features(d, x), y, sigma_noise=sigma_noise )
    return mu, sigma

In [ ]:
mu, sigma = train_poly_model(2, np.arange(1, len(x_train)+1), np.log(x_train))

In [ ]:
xs=np.arange(1, len(x_all) + 1)

# Посэмплируем и порисуем прямые
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((0, 20))
myplot_sample_lines(ax, 2, mu, sigma, xs, n=50)
ax.plot(xs, np.log(x_all) )
ax.vlines(len(x_train), 0, 15, linestyle="dotted")
ax.set_ylim((0, 13))
# plt.savefig("linregr_bayes9.pdf", bbox_inches="tight")

In [ ]:
xs = np.arange(1, 1000)
d = 2
n = 20

w_sample = np.random.multivariate_normal(mu, sigma, n)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((0, 18))

for w in w_sample:
    ax.plot(xs, np.dot(w, get_poly_features(d, xs)), 'k-', lw=.2, alpha=.5)

ax.plot(xs[:len(x_all)], np.log(x_all) )
ax.vlines(len(x_train), 0, 15, linestyle="dotted")
ax.set_ylim((0, 20))
# plt.savefig("linregr_bayes9.pdf", bbox_inches="tight")

In [ ]:
fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
# ax.set_ylim((0, 18))

cumulative_predictions = np.array([ np.cumsum( np.exp(np.dot(w, get_poly_features(d, xs))) ) for w in w_sample ])

for i, w in enumerate(w_sample):
    ax.plot(xs, cumulative_predictions[i], 'k-', lw=.4)

ax.plot(xs[:len(x_all)], x_all )
ax.vlines(len(x_train), 0, 15000, linestyle="dotted")
ax.set_ylim((0, 100000000))
ax.set_xlim((0, 300))

In [ ]:
n = 100000

w_sample = np.random.multivariate_normal(mu, sigma, n)
cumulative_predictions = np.array([ np.cumsum( np.exp(np.dot(w, get_poly_features(d, xs))) ) for w in w_sample ])
total_cases = np.array([cp[-1] for cp in cumulative_predictions if cp[-1] < 100000000])

print(len(total_cases), n)

fig = plt.figure(figsize=(20, 10))
ax = fig.add_subplot(111)
ax.hist(total_cases, bins=100)
# ax.set_xlim((0, 100000000))
plt.show()

In [ ]:
print("10-й процентиль: %d" % np.percentile(total_cases, 10))
print("90-й процентиль: %d" % np.percentile(total_cases, 90))
print("95-й процентиль: %d" % np.percentile(total_cases, 95))

## Байесовский выбор моделей (BIC)

In [ ]:
## Оверфиттинг
## Исходная функция
orig = lambda x : np.sin(2*x)

## X-координаты точек данных
xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
num_points = len(xd)

## Данные
data = orig(xd) + np.random.normal(0, .25, num_points)

## Для рисования
xs = np.arange(xd[0]-1.5, xd[-1]+1.5, 0.01)

## Обучаем модель с регуляризацией
@ignore_warnings(category=ConvergenceWarning)
def train_model(xs, ys, alpha=0, use_lasso=False):
    if alpha == 0:
        return linear_model.LinearRegression(fit_intercept=True).fit( xs, ys )
    else:
        if use_lasso:
            return linear_model.Lasso(alpha=alpha, fit_intercept=True).fit( xs, ys )
        else:
            return linear_model.Ridge(alpha=alpha, fit_intercept=True).fit( xs, ys )

## Выделение полиномиальных признаков
xs_d = np.vstack([xs ** i for i in range(1, num_points+1)]).transpose()
xd_d = np.vstack([xd ** i for i in range(1, num_points+1)]).transpose()

## Какие степени многочлена будем обучать и рисовать
set_of_powers = [ 3, 4, 10 ]

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-2, 2))
ax.scatter(xd, data, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

for d in set_of_powers:
    if d == 0:
        print(np.mean(data))
        ax.hlines(np.mean(data), xmin=xs[0], xmax=xs[-1], label="$d=0$", linestyle="dashed")
    else:
        cur_model = train_model( xd_d[:, :d], data )
        print(cur_model.coef_)
        ax.plot(xs, cur_model.predict( xs_d[:, :d] ), linewidth=2, label="$d=%d$" % d)

ax.legend(loc="upper center")

plt.show()

In [ ]:
def logL(model, xs, ys):
    yfit = model.predict(xs)
    return np.sum([ sp.stats.norm.logpdf(ys[i], loc=yfit[i], scale=.25) for i in range(ys.shape[0]) ])

def BIC(ll, N, k):
    return -2*ll + np.log(N)*k

def AIC(ll, N, k):
    if N > k+1:
        return -2*ll + 2*k + (2*k*k+2*k) / (N - k - 1)
    else:
        return -2*ll + 2*k + (2*k*k+2*k)

models = [ train_model( xd_d[:, :d], data ) for d in range(1, 11) ]
logLs = [logL(models[d-1], xd_d[:,:d], data) for d in range(1, 11)]
bics = [BIC(logLs[d-1], data.shape[0], d+1) for d in range(1, 11)]
aics = [AIC(logLs[d-1], data.shape[0], d+1) for d in range(1, 11)]

print("Логарифмы правдоподобий:\n%s" % logLs)
print("Значения AIC:\n%s" % aics)
print("Значения BIC:\n%s" % bics)
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
# ax.set_xlim((xs[0], xs[-1]))
# ax.set_ylim((-2, 2))
ax.plot(range(1, 11), logLs, label="Log likelihood")
ax.plot(range(1, 11), aics, label="AIC")
ax.plot(range(1, 11), bics, label="BIC")
ax.legend(fontsize=legend_fontsize)
# ax.set_ylim((-35, 100))
plt.show()

## Модельные методы классификации

In [ ]:
def sample_mixture(N, pi, mu1, sigma1, mu2, sigma2):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    res = np.zeros((N, 2))
    res[np.where(z == 1)] = np.random.multivariate_normal(mu1, sigma1, np.sum(z))
    res[np.where(z == 0)] = np.random.multivariate_normal(mu2, sigma2, N-np.sum(z))
    return z, res

def plot_points(ax, x, z, mu1, mu2):
    ax.scatter(x[np.where(z==1), 0], x[np.where(z==1), 1], marker='.', color='b')
    ax.scatter(x[np.where(z==0), 0], x[np.where(z==0), 1], marker='.', color='r')
    ax.scatter([mu1[0]], [mu1[1]], marker='*', s=120, color='b')
    ax.scatter([mu2[0]], [mu2[1]], marker='*', s=120, color='r')

def plot_ellipse(ax, mu, sigma, color):
    v, w = sp.linalg.eigh(sigma)
    u = w[0] / sp.linalg.norm(w[0])
    angle = np.arctan(u[1] / u[0])
    angle = 180 * angle / np.pi
    ell = mpl.patches.Ellipse(mu, 2 * v[0] ** 0.5, 2 * v[1] ** 0.5,
                              180 + angle, facecolor=color,
                              edgecolor='black', linewidth=2)
    ell.set_clip_box(ax.bbox)
    ell.set_alpha(0.2)
    ax.add_artist(ell)
    ax.scatter(mu[0], mu[1], marker='+', color=color, s=100)

mu1, sigma1 = np.array([-1, -.5]), np.array([[1, -.5], [-.5, 2]])
mu2, sigma2 = np.array([.5, 1]), np.array([[2, .5], [.5, .5]])
z, x = sample_mixture(100, 0.7, mu1, sigma1, mu2, sigma2)
test_z, test_x = sample_mixture(100, 0.7, mu1, sigma1, mu2, sigma2)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
plot_ellipse(ax, mu2, sigma2, 'r')
plot_ellipse(ax, mu1, sigma1, 'b')
plot_points(ax, x, z, mu1, mu2)

In [ ]:
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.discriminant_analysis import QuadraticDiscriminantAnalysis

lda = LinearDiscriminantAnalysis(store_covariance=True)
z_lda = lda.fit(x, z).predict(x)

qda = QuadraticDiscriminantAnalysis(store_covariance=True)
z_qda = qda.fit(x, z).predict(x)

In [ ]:
from matplotlib import colors
cmap = colors.LinearSegmentedColormap(
    'red_blue_classes',
    {'red': [(0, 1, 1), (1, 0.7, 0.7)],
     'green': [(0, 0.7, 0.7), (1, 0.7, 0.7)],
     'blue': [(0, 0.7, 0.7), (1, 1, 1)]})

def plot_colormesh(ax, model):
    nx, ny = 100, 100
    x_min, x_max = plt.xlim()
    y_min, y_max = plt.ylim()
    xx, yy = np.meshgrid(np.linspace(x_min, x_max, nx), np.linspace(y_min, y_max, ny))
    Z = model.predict_proba(np.c_[xx.ravel(), yy.ravel()])
    Z = Z[:, 1].reshape(xx.shape)
    plt.pcolormesh(xx, yy, Z, cmap=cmap,
                   norm=colors.Normalize(0., 1.), zorder=0)
    plt.contour(xx, yy, Z, [0.5], linewidths=2., colors='white')    

In [ ]:
print("LDA priors: %s" % lda.priors_)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)
plot_ellipse(ax, lda.means_[0], lda.covariance_, 'r')
plot_ellipse(ax, lda.means_[1], lda.covariance_, 'b')
plot_colormesh(ax, lda)
plt.show()

In [ ]:
print("QDA priors: %s" % qda.priors_)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)
plot_ellipse(ax, qda.means_[0], qda.covariance_[0], 'r')
plot_ellipse(ax, qda.means_[1], qda.covariance_[1], 'b')
plot_colormesh(ax, qda)
plt.show()

## Логистическая регрессия

In [ ]:
logregr = linear_model.LogisticRegression(class_weight='balanced')
z_logregr = logregr.fit(x, z).predict(x)

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)
plot_colormesh(ax, logregr)
plt.show()

In [ ]:
def plot_decision_boundary(ax, model, color, label):
    nx, ny = 100, 100
    x_min, x_max = plt.xlim()
    y_min, y_max = plt.ylim()
    xx, yy = np.meshgrid(np.linspace(x_min, x_max, nx), np.linspace(y_min, y_max, ny))
    Z = model.predict_proba(np.c_[xx.ravel(), yy.ravel()])
    Z = Z[:, 1].reshape(xx.shape)
    p = ax.contour(xx, yy, Z, [0.5], linewidths=1.5, colors=[color])
    p.collections[0].set_label(label)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)
p = plot_decision_boundary(ax, lda, palette[0], "LDA")
plot_decision_boundary(ax, qda, palette[1], "QDA")
plot_decision_boundary(ax, logregr, palette[2], "Логистическая регрессия")
plt.legend()
plt.show()

## Метод опорных векторов: линейные SVM

In [ ]:
def sample_mixture(N, pi, mu1, sigma1, mu2, sigma2):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    res = np.zeros((N, 2))
    res[np.where(z == 1)] = np.random.multivariate_normal(mu1, sigma1, np.sum(z))
    res[np.where(z == 0)] = np.random.multivariate_normal(mu2, sigma2, N-np.sum(z))
    return z, res

def sample_two_classes(mu1, sigma1, mu2, sigma2, pi=0.5, N=200, Ntest=None):
    z, x = sample_mixture(N, pi, mu1, sigma1, mu2, sigma2)
    if Ntest is None:
        return z, x
    else:
        test_z, test_x = sample_mixture(Ntest, pi, mu1, sigma1, mu2, sigma2)
        return z, x, test_z, test_x

def plot_points(ax, x, z, mu1=None, mu2=None):
    ax.scatter(x[np.where(z==1), 0], x[np.where(z==1), 1], marker='.', color='b')
    ax.scatter(x[np.where(z==0), 0], x[np.where(z==0), 1], marker='.', color='r')
    if mu1 is not None:
        if mu1.ndim == 1:
            ax.scatter([mu1[0]], [mu1[1]], marker='*', s=120, color='b')
        else:
            ax.scatter(mu1[:, 0], mu1[:, 1], marker='*', s=120, color='b')
    if mu2 is not None:
        if mu2.ndim == 1:
            ax.scatter([mu2[0]], [mu2[1]], marker='*', s=120, color='r')
        else:
            ax.scatter(mu2[:, 0], mu2[:, 1], marker='*', s=120, color='r')

from matplotlib import colors
cmap = colors.LinearSegmentedColormap(
    'red_blue_classes',
    {'red': [(0, 1, 1), (1, 0.7, 0.7)],
     'green': [(0, 0.7, 0.7), (1, 0.7, 0.7)],
     'blue': [(0, 0.7, 0.7), (1, 1, 1)]})

def plot_ellipse(ax, mu, sigma, color):
    v, w = sp.linalg.eigh(sigma)
    u = w[0] / sp.linalg.norm(w[0])
    angle = np.arctan(u[1] / u[0])
    angle = 180 * angle / np.pi
    ell = mpl.patches.Ellipse(mu, 2 * v[0] ** 0.5, 2 * v[1] ** 0.5,
                              180 + angle, facecolor=color,
                              edgecolor='black', linewidth=2)
    ell.set_clip_box(ax.bbox)
    ell.set_alpha(0.2)
    ax.add_artist(ell)
    ax.scatter(mu[0], mu[1], marker='+', color=color, s=100)

def get_meshgrid(nx=200, ny=200):
    x_min, x_max = plt.xlim()
    y_min, y_max = plt.ylim()
    return np.meshgrid(np.linspace(x_min, x_max, nx), np.linspace(y_min, y_max, ny))

def plot_colormesh(ax, model):
    xx, yy = get_meshgrid()
    Z = model.predict_proba(np.c_[xx.ravel(), yy.ravel()])
    Z = Z[:, 1].reshape(xx.shape)
    plt.pcolormesh(xx, yy, Z, cmap=cmap,
                   norm=colors.Normalize(0., 1.), zorder=0)
    plt.contour(xx, yy, Z, [0.5], linewidths=2., colors='white')

def plot_colormesh_svm(ax, model):
    xx, yy = get_meshgrid()
    Z = model.decision_function(np.c_[xx.ravel(), yy.ravel()]).reshape(xx.shape)
    ax.pcolormesh(xx, yy, Z, cmap=cmap,
                   norm=colors.Normalize(0., 1.), zorder=0)
    ax.contour(xx, yy, Z, [-1, 0, 1], linewidths=2., colors='white', linestyles=['--', '-', '--'])

def plot_svm_decision(ax, model, xx, yy):
    Z = model.decision_function(np.c_[xx.ravel(), yy.ravel()]).reshape(xx.shape)
    ax.contour(xx, yy, Z, [0], linewidths=.5, colors='black', linestyles=['-'])

def plot_svm_decisions(ax, models):
    xx, yy = get_meshgrid()
    for model in models:
        plot_svm_decision(ax, model, xx, yy)

In [ ]:
mu1, sigma1 = np.array([-1, -.5]), .25*np.array([[1, -.5], [-.5, 2]])
mu2, sigma2 = np.array([2.5, 1]), .25*np.array([[2, -1.2], [-1.2, 2.5]])

z, x = sample_two_classes(mu1, sigma1, mu2, sigma2)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)

plt.show()

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1, mu2)

xs = np.arange(-3, 6)
ax.plot(xs, xs*-.75 + 1.2, color="black", linewidth=.75, linestyle="--")
ax.plot(xs, xs*-1. + .8, color="gray", linewidth=.5)
ax.plot(xs, xs*-20 + 3.8, color="gray", linewidth=.5)
ax.plot(xs, xs*-5 + 2.8, color="gray", linewidth=.5)
ax.plot(xs, xs*-2.52 + 1.89, color="black", linewidth=1.5)
ax.plot(xs, xs*-1.7 + 2, color="gray", linewidth=.5)
ax.plot(xs, xs*7.7 - 3.3, color="black", linewidth=.75, linestyle="--")
ax.set_xlim((-3, 5))
ax.set_ylim((-3, 3))

plt.show()

In [ ]:
from sklearn.svm import SVC

model = SVC(kernel='linear', C=1E100)
model.fit(x, z)

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
print("%d опорных векторов" % model.support_vectors_.shape[0])
ax.scatter( model.support_vectors_[:, 0], model.support_vectors_[:, 1], color='white', s=30 )
plot_points(ax, x, z, mu1, mu2)
plot_colormesh_svm(ax, model)

plt.show()

In [ ]:
-model.coef_[0][0] / model.coef_[0][1], -model.intercept_[0] / model.coef_[0][1]

## SVM с ошибками и регуляризатором

In [ ]:
z, x = sample_two_classes(mu1, 2*sigma1, mu2, 2*sigma2)

In [ ]:
z, x = sample_two_classes(mu1, 2*sigma1, mu2, 2*sigma2)
model = SVC(kernel='linear', C=1E12).fit(x, z)

fig = plt.figure(figsize=(15,8))
ax = fig.add_subplot(111)
print("%d опорных векторов" % model.support_vectors_.shape[0])
ax.scatter( model.support_vectors_[:, 0], model.support_vectors_[:, 1], color='white', s=30 )
plot_points(ax, x, z, mu1, mu2)
plot_colormesh_svm(ax, model)

plt.show()

In [ ]:
z, x = sample_two_classes(mu1, 3*sigma1, mu2, 3*sigma2)
model = SVC(kernel='linear', C=1E-1).fit(x, z)

fig = plt.figure(figsize=(15,8))
ax = fig.add_subplot(111)
print("%d опорных векторов" % model.support_vectors_.shape[0])
ax.scatter( model.support_vectors_[:, 0], model.support_vectors_[:, 1], color='white', s=30 )
plot_points(ax, x, z, mu1, mu2)
plot_colormesh_svm(ax, model)
plt.show()

In [ ]:
sigma_multiplier = 3
C = 1E-2
models = []
for _ in range(50):
    z, x = sample_two_classes(mu1, sigma_multiplier*sigma1, mu2, sigma_multiplier*sigma2)
    models.append( SVC(kernel='linear', C=C).fit(x, z) )

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
plot_ellipse(ax, mu1, 2*sigma_multiplier*sigma1, 'r')
plot_ellipse(ax, mu2, 2*sigma_multiplier*sigma2, 'b')
# plot_points(ax, x, z, mu1, mu2)
ax.set_xlim((-2, 4))
ax.set_ylim((-2, 4))
plot_svm_decisions(ax, models)

plt.show()

## Kernel trick

In [ ]:
def sample_rings(rad_inner, rad_outer, rad_inner2, rad_outer2, pi=0.5, N=200, Ntest=None):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    rs = ( rad_inner + (rad_inner - rad_outer) * np.random.rand(np.sum(z)) )
    thetas = 2 * np.pi * np.random.rand(np.sum(z))
    rs2 = ( rad_inner2 + (rad_inner2 - rad_outer2) * np.random.rand(N - np.sum(z)) )
    thetas2 = 2 * np.pi * np.random.rand(N - np.sum(z))
    
    res = np.zeros((N, 2))
    res[np.where(z == 1)] = np.array([ rs * np.cos(thetas), rs * np.sin(thetas) ]).T
    res[np.where(z == 0)] = np.array([ rs2 * np.cos(thetas2), rs2 * np.sin(thetas2) ]).T
    return z, res

def sample_mixture(N, pi, mu1, sigma1, mu2, sigma2):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    res = np.zeros((N, 2))
    res[np.where(z == 1)] = np.random.multivariate_normal(mu1, sigma1, np.sum(z))
    res[np.where(z == 0)] = np.random.multivariate_normal(mu2, sigma2, N-np.sum(z))
    return z, res

def sample_mixtures(mu0=np.array([ [-1,-1], [1,1] ]), sigma0=2, k=5, pi=0.5, df=4, N=200, Ntest=None):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    res = np.zeros((N, 2))
    mus, sigmas = [], []
    for i, n in zip(range(2), [N-np.sum(z), np.sum(z)]):
        mus.append( np.random.multivariate_normal(mu0[i], sigma0 * np.identity(2), k) )
        sigmas.append( sp.stats.invwishart.rvs(df, np.identity(2), size=k) )
        mixture_ind = np.random.randint(k, size=n)
        cur_res = np.zeros((n, 2))
        for j in range(k):
            cur_indices = np.where(mixture_ind == j)[0]
            cur_res[cur_indices] = np.random.multivariate_normal(mus[-1][j], sigmas[-1][j], len(cur_indices))
        res[np.where(z == i)] = cur_res
    return z, res, mus, sigmas

In [ ]:
z, x = sample_rings(0, 3, 5, 6)

model = SVC(kernel='linear', C=1E-1).fit(x, z)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
plot_points(ax, x, z)
plot_colormesh_svm(ax, model)
plt.show()

In [ ]:
C = 1e-1


model = SVC(kernel='poly', degree=2, C=C).fit(x, z)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
print("%d опорных векторов" % model.support_vectors_.shape[0])
ax.scatter( model.support_vectors_[:, 0], model.support_vectors_[:, 1], color='white', s=40 )
plot_points(ax, x, z)
plot_colormesh_svm(ax, model)
plt.show()

In [ ]:
z, x, mus, sigmas = sample_mixtures(sigma0=5, N=500)

In [ ]:
C = 1e3
model = SVC(kernel='rbf', C=C).fit(x, z)

fig = plt.figure(figsize=(15,9))
ax = fig.add_subplot(111)
print("%d опорных векторов" % model.support_vectors_.shape[0])
ax.scatter( model.support_vectors_[:, 0], model.support_vectors_[:, 1], color='white', s=40 )
plot_points(ax, x, z, mu1=mus[1], mu2=mus[0])
plot_colormesh_svm(ax, model)
plt.show()

## Relevance vector machines

In [ ]:
from sklearn.svm import SVC
import sklearn_rvm
from sklearn_rvm import EMRVC, EMRVR

In [ ]:
def sample_mixture(N, pi, mu1, sigma1, mu2, sigma2):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    res = np.zeros((N, 2))
    res[np.where(z == 1)] = np.random.multivariate_normal(mu1, sigma1, np.sum(z))
    res[np.where(z == 0)] = np.random.multivariate_normal(mu2, sigma2, N-np.sum(z))
    return z, res

def sample_two_classes(mu1, sigma1, mu2, sigma2, pi=0.5, N=200, Ntest=None):
    z, x = sample_mixture(N, pi, mu1, sigma1, mu2, sigma2)
    if Ntest is None:
        return z, x
    else:
        test_z, test_x = sample_mixture(Ntest, pi, mu1, sigma1, mu2, sigma2)
        return z, x, test_z, test_x

def plot_points(ax, x, z, mus=None, mu1=None, mu2=None, sigmas=None, points_alpha=1.0, colors=['r', 'b', 'g', 'magenta', 'grey', 'purple', 'darkgreen']):
    print(set(z))
    for i in set(z):
        ax.scatter(x[np.where(z==i), 0], x[np.where(z==i), 1], marker='.', color=colors[i % 7], alpha=points_alpha)
        if sigmas is not None:
            plot_ellipse(ax, mus[i], sigmas[i], colors[i % 7])
    if mus is not None:
        for i in range(mus.shape[0]):
            ax.scatter([mus[i, 0]], [mus[i, 1]], marker='*', s=200, color=colors[i % 7])
    if mu1 is not None:
        for i in range(mu1.shape[0]):
            ax.scatter([mu1[i, 0]], [mu1[i, 1]], marker='*', s=200, color=colors[0])
    if mu2 is not None:
        for i in range(mu2.shape[0]):
            ax.scatter([mu2[i, 0]], [mu2[i, 1]], marker='*', s=200, color=colors[1])

from matplotlib import colors
cmap = colors.LinearSegmentedColormap(
    'red_blue_classes',
    {'red': [(0, 1, 1), (1, 0.7, 0.7)],
     'green': [(0, 0.7, 0.7), (1, 0.7, 0.7)],
     'blue': [(0, 0.7, 0.7), (1, 1, 1)]})

def plot_ellipse(ax, mu, sigma, color):
    v, w = sp.linalg.eigh(sigma)
    u = w[0] / sp.linalg.norm(w[0])
    angle = np.arctan(u[1] / u[0])
    angle = 180 * angle / np.pi
    ell = mpl.patches.Ellipse(mu, 2 * v[0] ** 0.5, 2 * v[1] ** 0.5,
                              180 + angle, facecolor=color,
                              edgecolor='black', linewidth=2)
    ell.set_clip_box(ax.bbox)
    ell.set_alpha(0.2)
    ax.add_artist(ell)
    ax.scatter(mu[0], mu[1], marker='+', color=color, s=100)

def get_meshgrid(nx=200, ny=200):
    x_min, x_max = plt.xlim()
    y_min, y_max = plt.ylim()
    return np.meshgrid(np.linspace(x_min, x_max, nx), np.linspace(y_min, y_max, ny))

def plot_colormesh(ax, model):
    xx, yy = get_meshgrid()
    Z = model.predict_proba(np.c_[xx.ravel(), yy.ravel()])
    Z = Z[:, 1].reshape(xx.shape)
    plt.pcolormesh(xx, yy, Z, cmap=cmap,
                   norm=colors.Normalize(0., 1.), zorder=0)
    plt.contour(xx, yy, Z, [0.5], linewidths=2., colors='white')

def plot_colormesh_svm(ax, model):
    xx, yy = get_meshgrid()
    Z = model.decision_function(np.c_[xx.ravel(), yy.ravel()]).reshape(xx.shape)
    ax.pcolormesh(xx, yy, Z, cmap=cmap,
                   norm=colors.Normalize(0., 1.), zorder=0)
    ax.contour(xx, yy, Z, [-1, 0, 1], linewidths=2., colors='white', linestyles=['--', '-', '--'])

def plot_svm_decision(ax, model, xx, yy):
    Z = model.decision_function(np.c_[xx.ravel(), yy.ravel()]).reshape(xx.shape)
    ax.contour(xx, yy, Z, [0], linewidths=.5, colors='black', linestyles=['-'])

def plot_svm_decisions(ax, models):
    xx, yy = get_meshgrid()
    for model in models:
        plot_svm_decision(ax, model, xx, yy)
        
def sample_rings(rad_inner, rad_outer, rad_inner2, rad_outer2, pi=0.5, N=200, Ntest=None):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    rs = ( rad_inner + (rad_inner - rad_outer) * np.random.rand(np.sum(z)) )
    thetas = 2 * np.pi * np.random.rand(np.sum(z))
    rs2 = ( rad_inner2 + (rad_inner2 - rad_outer2) * np.random.rand(N - np.sum(z)) )
    thetas2 = 2 * np.pi * np.random.rand(N - np.sum(z))
    
    res = np.zeros((N, 2))
    res[np.where(z == 1)] = np.array([ rs * np.cos(thetas), rs * np.sin(thetas) ]).T
    res[np.where(z == 0)] = np.array([ rs2 * np.cos(thetas2), rs2 * np.sin(thetas2) ]).T
    return z, res

def sample_mixture(N, pi, mu1, sigma1, mu2, sigma2):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    res = np.zeros((N, 2))
    res[np.where(z == 1)] = np.random.multivariate_normal(mu1, sigma1, np.sum(z))
    res[np.where(z == 0)] = np.random.multivariate_normal(mu2, sigma2, N-np.sum(z))
    return z, res

def sample_mixtures(mu0=np.array([ [-1,-1], [1,1] ]), sigma0=2, k=5, pi=0.5, df=4, N=200, Ntest=None):
    z = np.array( np.random.rand(N) < pi, dtype=int)
    res = np.zeros((N, 2))
    mus, sigmas = [], []
    for i, n in zip(range(2), [N-np.sum(z), np.sum(z)]):
        mus.append( np.random.multivariate_normal(mu0[i], sigma0 * np.identity(2), k) )
        sigmas.append( sp.stats.invwishart.rvs(df, np.identity(2), size=k) )
        mixture_ind = np.random.randint(k, size=n)
        cur_res = np.zeros((n, 2))
        for j in range(k):
            cur_indices = np.where(mixture_ind == j)[0]
            cur_res[cur_indices] = np.random.multivariate_normal(mus[-1][j], sigmas[-1][j], len(cur_indices))
        res[np.where(z == i)] = cur_res
    return z, res, mus, sigmas

def sample_oneclass_mixture(mu0=np.array([0, 0]), sigma0=2, k=5, pi=None, df=4, N=200, Ntest=None):
    mus = np.random.multivariate_normal(mu0, sigma0 * np.identity(2), k)
    sigmas = sp.stats.invwishart.rvs(df, np.identity(2), size=k)
    mixture_ind = np.random.randint(k, size=N)
    res = np.zeros((N, 2))
    for j in range(k):
        cur_indices = np.where(mixture_ind == j)[0]
        res[cur_indices] = np.random.multivariate_normal(mus[j], sigmas[j], len(cur_indices))
    return np.eye(k)[mixture_ind], res, mus, sigmas


In [ ]:
## Оверфиттинг
## Исходная функция
orig = lambda x : np.sin(2*x)

## X-координаты точек данных
xd = np.array([-3, -2, -1, -0.5, 0, 0.5, 1, 1.5, 2.5, 3, 4]) / 2
num_points = len(xd)

## X-координаты точек данных
xd_large = np.arange(-1.5, 2, 0.05)
num_points_l = len(xd_large)

## Данные
data = orig(xd) + np.random.normal(0, .25, num_points)
data_dict = { x : val for x, val in zip(xd, data) }
data_large = orig(xd_large) + np.random.normal(0, .25, num_points_l)
data_large_dict = { x : val for x, val in zip(xd_large, data_large) }

## Для рисования
xs = np.arange(xd[0]-1.5, xd[-1]+1.5, 0.01)

## Обучаем модель с регуляризацией
@ignore_warnings(category=ConvergenceWarning)
def train_model(xs, ys, alpha=0, use_lasso=False):
    if alpha == 0:
        return linear_model.LinearRegression(fit_intercept=True).fit( xs, ys )
    else:
        if use_lasso:
            return linear_model.Lasso(alpha=alpha, fit_intercept=True).fit( xs, ys )
        else:
            return linear_model.Ridge(alpha=alpha, fit_intercept=True).fit( xs, ys )

In [ ]:
## Выделение полиномиальных признаков
xs_d = np.vstack([xs ** i for i in range(1, num_points+1)]).transpose()
xd_d = np.vstack([xd ** i for i in range(1, num_points+1)]).transpose()

## Какие степени многочлена будем обучать и рисовать
set_of_powers = [ 3, 10 ]

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-2, 2))
ax.scatter(xd, data, marker='*', s=120)
ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")

for d in set_of_powers:
    if d == 0:
        print(np.mean(data))
        ax.hlines(np.mean(data), xmin=xs[0], xmax=xs[-1], label="$d=0$", linestyle="dashed")
    else:
        cur_model = train_model( xd_d[:, :d], data )
        print(cur_model.coef_)
        ax.plot(xs, cur_model.predict( xs_d[:, :d] ), linewidth=2, label="$d=%d$" % d)

ax.legend(loc="upper center", fontsize=legend_fontsize)

plt.show()

In [ ]:
xx, yy, dd = xd, data, data_dict
# xx, yy, dd = xd_large, data_large, data_large_dict
model = EMRVR(kernel="rbf", verbose=True)
model.fit(xx.reshape(-1, 1), yy)

In [ ]:
predicted_y, predicted_std = model.predict(xs.reshape(-1, 1), return_std=True)

In [ ]:
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
print("%d релевантных векторов" % model.relevance_vectors_.shape[0])
ax = fig.add_subplot(111)
ax.set_xlim((xs[0], xs[-1]))
ax.set_ylim((-2, 2))
ax.scatter(xx, yy, marker='*', s=100)
ax.plot(xs, orig(xs), linewidth=1, label="Исходная функция", color="black")
ax.scatter( [ x[0] for x in model.relevance_vectors_], [dd[x[0]] for x in model.relevance_vectors_ ], color='red', marker='*', s=150 )
ax.plot( xs, predicted_y, color=palette[2], label="Предсказание RVM" )
ax.fill_between(xs, predicted_y-predicted_std, predicted_y+predicted_std, color=palette[2], alpha=.3)
ax.legend()
# plot_points(ax, x, z, mu1=mus[1], mu2=mus[0])
# plot_colormesh_svm(ax, model)
# plt.savefig("svm-rvm1.pdf", bbox_inches="tight")
plt.show()

In [ ]:
xs2 = np.arange(xd[0]-15, xd[-1]+15, 0.1)
predicted_y2, predicted_std2 = model.predict(xs2.reshape(-1, 1), return_std=True)

fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
print("%d релевантных векторов" % model.relevance_vectors_.shape[0])
ax = fig.add_subplot(111)
ax.set_xlim((xs2[0], xs2[-1]))
ax.set_ylim((-2, 2))
ax.scatter(xx, yy, marker='*', s=100)
ax.plot(xs2, orig(xs2), linewidth=1, label="Исходная функция", color="black")
ax.scatter( [ x[0] for x in model.relevance_vectors_], [dd[x[0]] for x in model.relevance_vectors_ ], color='red', marker='*', s=150 )
ax.plot( xs2, predicted_y2, color=palette[2], label="Предсказание RVM" )
ax.fill_between(xs2, predicted_y2-predicted_std2, predicted_y2+predicted_std2, color=palette[2], alpha=.3)
ax.legend()
plt.show()

In [ ]:
z, x, mus, sigmas = sample_mixtures(k=5, sigma0=5, N=200)

fig = plt.figure(figsize=(15,9))
ax = fig.add_subplot(111)
plot_points(ax, x, z, mu1=mus[0], mu2=mus[1])
plt.show()

In [ ]:
model = EMRVC(kernel="rbf", n_iter_posterior=6).fit(x, z)

In [ ]:
fig = plt.figure(figsize=(15,9))
ax = fig.add_subplot(111)
print("%d релевантных векторов" % model.relevance_vectors_.shape[0])
ax.scatter( model.relevance_vectors_[:, 0], model.relevance_vectors_[:, 1], color='white', s=40 )
plot_points(ax, x, z, mu1=mus[0], mu2=mus[1])
plot_colormesh(ax, model)
plt.show()

In [ ]:
model_svm = SVC(kernel="rbf", C=1e2).fit(x, z)

fig = plt.figure(figsize=(15,9))
ax = fig.add_subplot(111)
print("%d опорных векторов" % model_svm.support_vectors_.shape[0])
ax.scatter( model_svm.support_vectors_[:, 0], model_svm.support_vectors_[:, 1], color='white', s=40 )
plot_points(ax, x, z, mu1=mus[0], mu2=mus[1])
plot_colormesh_svm(ax, model_svm)
plt.show()

## EM-алгоритм для кластеризации

In [ ]:
k = 4
z, x, true_mus, true_sigmas = sample_oneclass_mixture(k=k, sigma0=2, df=20, N=300)

fig = plt.figure(figsize=(15,8))
ax = fig.add_subplot(111)
plot_points(ax, x, np.argmax(z, axis=1), mus=true_mus, sigmas=2 * true_sigmas, points_alpha=.5)
plt.show()

In [ ]:
def e_step(xs, pis, mus, sigmas):
    k = mus.shape[0]
    z = np.array([ pis[i] * sp.stats.multivariate_normal.pdf(xs, mean=mus[i], cov=sigmas[i]) for i in range(k) ])
    ## здесь z_{nk} = p(C_k)p(x_n|C_k)
    z = np.divide( z, np.sum(z, axis=0) ).T
    ## z_{nk} = p(C_k|x_n)
    return z

def m_step(xs, z):
    k = z.shape[1]
    pis = np.sum(z, axis=0) / np.sum(z)
    mus = np.array([np.average(xs, weights=z[:,i], axis=0) for i in range(k)])
    sigmas = np.array([np.cov(xs.T, aweights=z[:,i]) for i in range(k)])
    return pis, mus, sigmas

def loglikelihood(xs, pis, mus, sigmas):
    k = mus.shape[0]
    return np.sum(np.log(np.sum(np.array([ pis[i] * sp.stats.multivariate_normal.pdf(xs, mean=mus[i], cov=sigmas[i]) for i in range(k) ]), axis=0)))

In [ ]:
k = 4
mus = x[ np.random.choice(x.shape[0], size=k, replace=False), : ]
sigmas = np.array( [ np.identity(2) for _ in range(k) ] )
pis = (1./k) * np.ones(k)
z = e_step( x, pis, mus, sigmas)

fig = plt.figure(figsize=(15,8))
ax = fig.add_subplot(111)
plot_points(ax, x, np.argmax(z, axis=1), mus=mus, sigmas=2 * sigmas, points_alpha=.5)
plt.show()

In [ ]:
z = e_step( x, pis, mus, sigmas)
# print(z)
new_pis, new_mus, new_sigmas = m_step(x, z)
print(new_pis)
print(loglikelihood(x, new_pis, new_mus, new_sigmas))
fig = plt.figure(figsize=(15,8))
ax = fig.add_subplot(111)
plot_points(ax, x, np.argmax(z, axis=1), mus=new_mus, sigmas=2 * new_sigmas, points_alpha=.5)
plt.show()
pis, mus, sigmas = new_pis, new_mus, new_sigmas

In [ ]:
k = 15
mus = x[ np.random.choice(x.shape[0], size=k, replace=False), : ]
sigmas = np.array( [ np.identity(2) for _ in range(k) ] )
pis = (1./k) * np.ones(k)
z = e_step( x, pis, mus, sigmas)

## EM-алгоритм
old_logl, new_logl = -np.inf, -np.inf
for iIter in range(5000):
    old_logl = new_logl
    z = e_step( x, pis, mus, sigmas)
    # print(z)
    new_pis, new_mus, new_sigmas = m_step(x, z)
    # fig = plt.figure(figsize=(15,8))
    # ax = fig.add_subplot(111)
    # plot_points(ax, x, np.argmax(z, axis=1), mus=new_mus, sigmas=2 * new_sigmas, points_alpha=.5)
    # plt.show()
    pis, mus, sigmas = new_pis, new_mus, new_sigmas
    new_logl = loglikelihood(x, pis, mus, sigmas)
    print("Логарифм правдоподобия на итерации %03d: %.6f" % (iIter, new_logl) )
    if np.abs(new_logl - old_logl) < 0.000001:
        break

print("После %d итераций правдоподобие = %.6f" % (iIter, new_logl) )

In [ ]:
print(pis)
fig = plt.figure(figsize=(15,8))
ax = fig.add_subplot(111)
plot_points(ax, x, np.argmax(z, axis=1), mus=new_mus, sigmas=2 * new_sigmas, points_alpha=.5)
plt.show()

In [ ]:
likelihoods = {}

for k in range(2, 15):
    mus = x[ np.random.choice(x.shape[0], size=k, replace=False), : ]
    sigmas = np.array( [ np.identity(2) for _ in range(k) ] )
    pis = (1./k) * np.ones(k)

    ## EM-алгоритм
    old_logl, new_logl = -np.inf, -np.inf
    for iIter in range(50000):
        old_logl = new_logl
        z = e_step( x, pis, mus, sigmas)
        new_pis, new_mus, new_sigmas = m_step(x, z)
        pis, mus, sigmas = new_pis, new_mus, new_sigmas
        new_logl = loglikelihood(x, pis, mus, sigmas)
        if np.abs(new_logl - old_logl) < 0.00001:
            break
    print("k = %d\tПравдоподобие = %.6f" % (k, new_logl) )
    likelihoods[k] = new_logl

In [ ]:
def BIC(ll, N, d):
    return -2*ll + np.log(N)*d

def AIC(ll, N, d):
    if N > d+1:
        return -2*ll + 2*d + (2*d*d+2*d) / (N - d - 1)
    else:
        return -2*ll + 2*d + (2*d*d+2*d)

In [ ]:
logLs = [ likelihoods[k] for k in sorted(likelihoods.keys()) ]
bics = [ BIC(likelihoods[k], x.shape[0], k-1 + k*( 2 + 3 ) ) for k in sorted(likelihoods.keys()) ]
aics = [ AIC(likelihoods[k], x.shape[0], k-1 + k*( 2 + 3 )  ) for k in sorted(likelihoods.keys()) ]

print("Логарифмы правдоподобий:\n%s" % logLs)
print("Значения AIC:\n%s" % aics)
print("Значения BIC:\n%s" % bics)
fig = plt.figure(figsize=figsize)
ax = fig.add_subplot(111)
ax.plot(sorted(likelihoods.keys()), logLs, label="Log likelihood")
ax.plot(sorted(likelihoods.keys()), aics, label="AIC")
ax.plot(sorted(likelihoods.keys()), bics, label="BIC")
ax.legend(fontsize=legend_fontsize)
# ax.set_ylim((-320, 800))
plt.show()

## EM для кластеризации строк

In [ ]:
hamming_distance = lambda w1, w2: sum(s1 != s2 for s1, s2 in zip(w1, w2))
hamming_distance = np.vectorize(hamming_distance)

whole_wordset = Counter()
iLine = 0
with open('/media/snikolenko/data/wiki.processed') as f:
    for line in f:
        iLine += 1
        whole_wordset.update(line.split())
        if iLine == 10000:
            break

In [ ]:
m = 7
wordset = { k : v for k,v in whole_wordset.items() if len(k) == m }
all_words = np.array([k for k in wordset])

In [ ]:
seed_words = np.random.choice([ w for w in all_words if whole_wordset[w] > 20], 20, replace=False)
print(sorted(seed_words))

In [ ]:
words = np.array([ w for w in all_words if np.min(hamming_distance(w, seed_words)) < 3 ])

In [ ]:
symbols = np.array([ a for a in set([ s for w in words for s in w ])])
smap = { v : i for (i, v) in enumerate(symbols) }
iwords = np.array([[smap[s] for s in w] for w in words])
ns = len(symbols)

In [ ]:
ns, sorted(seed_words), sorted(words)

In [ ]:
k = 20
num_samples = 2
sample_words = words[ np.random.choice(words.shape[0], size=num_samples*k, replace=False) ]
ps = (1./float(ns)) * np.ones(shape=(k, m, ns))
for i in range(k):
    for j in range(num_samples):
        for iS, s in enumerate(sample_words[num_samples*i + j]):
            ps[i, iS, smap[s]] += 1
ps_sums = np.sum(ps, axis=2)
for i in range(ps.shape[0]):
    for j in range(ps.shape[1]):
        ps[i, j, :] = ps[i, j, :] / ps_sums[i, j]
pis = (1./k) * np.ones(k)

In [ ]:
def e_step(xs, pis, logps):
    z = np.sum( np.array([ [logps[:, i, iwords[j][i]] for i in range(m)] for j in range(iwords.shape[0]) ]), axis = 1 ) + np.log(pis)
    # ( ln q1 - ln(sum(exp(lq)))  ln q2 ... ln qK )
    z = z - np.logaddexp.reduce(z, axis=1).reshape(-1, 1)
    return z

def m_step(iwords, zs):
    z = np.exp(zs)
    pis = np.sum(z, axis=0) / np.sum(z)
    new_ps = np.ones(shape=(k, m, ns))
    for i in range(iwords.shape[0]):
        for ik in range(k):
            for im in range(m):
                new_ps[ik, im, iwords[i][im]] += z[i, ik]
    new_ps = np.divide( new_ps, np.sum( new_ps, axis = 2 ).reshape(k, m, 1) )
    return pis, new_ps

def print_clusters(z):
    zs = np.exp(z)
    for ik in range(k):
        print("Кластер %d:\n%s\n" % (ik, " ".join(np.sort([words[i] for i in range(z.shape[0]) if (zs[i, ik] > 0.7)]))))

In [ ]:
## один шаг EM-алгоритма; повторять по необходимости
z = e_step(iwords, pis, np.log(ps))
pis, ps = m_step(iwords, z)
print(pis)
print_clusters(z)

In [ ]:
for iIter in range(5):
    print("\n\n\t=== Итерация %d ===\n" % iIter)
    z = e_step(iwords, pis, np.log(ps))
    pis, ps = m_step(iwords, z)
    print(pis)
    print_clusters(z)